# World Governance Indicators and Hofstede Cultural Indicators

This notebook is to join these datasets together, selecting 2019 estimate data for WGI and 2015 indicators for the hofstede dataset.

First, we set our environment and constants

In [334]:
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

WGI_SHEET_NAMES = ['VoiceandAccountability', 'Political StabilityNoViolence', 'GovernmentEffectiveness', 'RegulatoryQuality', 'RuleofLaw', 'ControlofCorruption']

SOURCE_DATA = r"../02. Source Data/"
CLEANSED_DATA = r"../03. Cleansed Data/"
WGI_DATA = SOURCE_DATA + r"01 Suggested/Worldwide governance indicators/wgidataset.xlsx"
HOFSTEDE_DATA = SOURCE_DATA + r'01 Suggested/Hofstede national culture dimensions (2015)/6-dimensions-for-website-2015-08-16.xls'
WGI_CLEANSED = r"../03. Cleansed Data/wgi_prepped.csv"
HOFSTEDE_CLEANSED = r"../03. Cleansed Data/hofstede_prepped.csv"
WGI_HOFSTEDE_CLEANSED = r"../03. Cleansed Data/wgi_hofstede.csv"

## WGI Dataset

Each sheet in the workbook is a separate dataset, for 1996-2019. We're only interested in 2015 and the estimate column. We also notice that there are some country names that need to be cleaned.

In [277]:
wgi_dataset = {s: pd.read_excel(WGI_DATA, s, header=[13,14], index_col=[0,1]) for s in WGI_SHEET_NAMES}
# example of dataset:
wgi_dataset['VoiceandAccountability'].head()

1996                                          1998  \
Code             Estimate    StdErr NumSrc  Rank Lower  Upper  Estimate   
Aruba       ABW       NaN       NaN    NaN   NaN   NaN    NaN       NaN   
Andorra     ADO  1.563217  0.291691    3.0  98.5  81.5  100.0  1.528759   
Afghanistan AFG -1.908540  0.261457    4.0   1.0   0.0    9.5 -2.039301   
Angola      AGO -1.578164  0.208810    6.0   6.0   0.5   13.0 -1.411879   
Anguilla    AIA       NaN       NaN    NaN   NaN   NaN    NaN       NaN   

                                             ...   2018                        \
Code               StdErr NumSrc       Rank  ... NumSrc       Rank      Lower   
Aruba       ABW       NaN    NaN        NaN  ...    1.0  91.625618  77.339905   
Andorra     ADO  0.291445    3.0  97.512436  ...    2.0  83.251228  69.458130   
Afghanistan AFG  0.256090    4.0   0.497512  ...   10.0  20.689655  13.793103   
Angola      AGO  0.214446    6.0   9.452736  ...   11.0  22.660099  16.256157   
Anguilla    AIA       NaN    NaN        NaN  ...    NaN        NaN        NaN   

                                2019                                         \
Code                 Upper  Estimate    StdErr NumSrc       Rank      Lower   
Aruba       ABW  99.507393  1.294189  0.268796    1.0  92.610840  73.891624   
Andorra     ADO  95.566505  1.139154  0.219417    2.0  87.192116  72.906403   
Afghanistan AFG  25.615763 -0.988032  0.127851   10.0  21.674877  15.763547   
Angola      AGO  27.586206 -0.777283  0.123522   11.0  25.615763  21.674877   
Anguilla    AIA        NaN       NaN       NaN    NaN        NaN        NaN   

                             
Code                  Upper  
Aruba       ABW  100.000000  
Andorra     ADO   96.059113  
Afghanistan AFG   25.123152  
Angola      AGO   30.049261  
Anguilla    AIA         NaN  

[5 rows x 126 columns]

In [278]:
def combine_multicol(df, name):
    df1 = df.copy()
    df1.columns = ['%s%s' % (a, '_%s' % b if b else '') for a, b in df1.columns]
    cols = [c for c in df1.columns if 'estimate' in c.lower() and '2019' in c.lower()]
    df2 = df1[cols]
    df2.columns = [c + "_" + name for c in df2.columns]
    return df2

In [279]:
wgi_dataset_merged_columns = {k: combine_multicol(wgi_dataset[k], k) for k in wgi_dataset.keys()}

In [280]:
full_wgi_2019 = pd.concat([v for v in wgi_dataset_merged_columns.values()], axis=1)
full_wgi_2019.columns = sheet_names
full_wgi_2019 = full_wgi_2019.rename_axis(['country', 'ctr'])
full_wgi_2019 = full_wgi_2019.reset_index()
full_wgi_2019 = full_wgi_2019.dropna() # we drop null values as they're irrelevant.
full_wgi_2019['country'] = full_wgi_2019['country'].str.lower()
full_wgi_2019['country'] = full_wgi_2019['country'].str.replace('korea, rep.', 'south korea')
full_wgi_2019['country'] = full_wgi_2019['country'].str.replace('korea, dem. rep.', 'north korea')
full_wgi_2019['country'] = full_wgi_2019['country'].str.replace('\,.*', '', regex=True)
full_wgi_2019 = full_wgi_2019.replace({'country': {'hong kong sar': 'hong kong',
                                                    'russian federation': 'russia'}})
full_wgi_2019.head()

country  ctr  VoiceandAccountability  Political StabilityNoViolence  \
0        aruba  ABW                1.294189                       1.357372   
1      andorra  ADO                1.139154                       1.615139   
2  afghanistan  AFG               -0.988032                      -2.649407   
3       angola  AGO               -0.777283                      -0.311101   
5      albania  ALB                0.151805                       0.118570   

   GovernmentEffectiveness  RegulatoryQuality  RuleofLaw  ControlofCorruption  
0                 1.029933           0.857360   1.263128             1.217238  
1                 1.908749           1.228176   1.579939             1.234392  
2                -1.463875          -1.120555  -1.713527            -1.401076  
3                -1.117144          -0.893871  -1.054343            -1.054683  
5                -0.061331           0.274380  -0.411179            -0.528758

In [290]:
ProfileReport(full_wgi_2019)

## Hofstede Data

Similar, we clean it. For the Hofstede data, Arab countries have been merged together. We create the missing countries using the same indicator values.

In [327]:
#data cleaning
hofstede_data = pd.read_excel(HOFSTEDE_DATA)
hofstede_data = hofstede_data.dropna() #drop NA', 'can't really replace NA with any number e.g. 0 as the indexes are sliding scales and 0 would essentially mean '0/100' as a score
hofstede_data = hofstede_data.reset_index(drop=True) #dropping irrelevant indicies
hofstede_data = hofstede_data.drop(['idv', 'mas','ivr'], axis=1)
arab_countries = ['Bahrain', 'Comoros', 'Djibouti', 'Kuwait', 'Lebanon', 'Libya', 'Mauritania', 'Oman', 'Palestine', 'Qatar', 'Somalia', 'Sudan', 'Syrian arab rep', 'Tunisia', 'United Arab Emirates','Yemen']
arab_pdi = [80.0]*len(arab_countries)
arab_uai = [68.0]*len(arab_countries)
arab_ltowvs = [23.0]*len(arab_countries)
arab_df = pd.DataFrame({'country': arab_countries,
                        'pdi': arab_pdi,
                        'uai': arab_uai,
                        'ltowvs': arab_ltowvs})
hofstede_data = hofstede_data.append(arab_df)
hofstede_data['country'] = hofstede_data['country'].str.lower()
hofstede_data['country'] = hofstede_data['country'].str.replace(' rep', ' republic')
hofstede_data = hofstede_data.replace({'country': {'u.s.a.': 'united states',
                                                            'great britain': 'united kingdom',
                                                            'korea south': 'south korea'}})
hofstede_data.tail()

ctr               country   pdi   uai  ltowvs
11  NaN                 sudan  80.0  68.0    23.0
12  NaN  syrian arab republic  80.0  68.0    23.0
13  NaN               tunisia  80.0  68.0    23.0
14  NaN  united arab emirates  80.0  68.0    23.0
15  NaN                 yemen  80.0  68.0    23.0

In [328]:
ProfileReport(hofstede_data)

Inner join of the datasets

In [329]:
common = hofstede_data.merge(full_dataset_2019,on=['country'])
common = common.drop('ctr_x', axis=1)
print(common.shape)

(77, 11)


See non-joining rows on hofstede side:

In [330]:
hofstede_data[(~hofstede_data.country.isin(common.country))]

ctr         country   pdi   uai  ltowvs
0  AFE     africa east  64.0  52.0    32.0
1  AFW     africa west  77.0  54.0     9.0
2  ARA  arab countries  80.0  68.0    23.0
8  NaN       palestine  80.0  68.0    23.0

See non-joining rows on governance side:

In [331]:
full_dataset_2019[(~full_dataset_2019.country.isin(common.country))]

country  ctr  VoiceandAccountability  Political StabilityNoViolence  \
0           aruba  ABW                1.294189                       1.357372   
1         andorra  ADO                1.139154                       1.615139   
2     afghanistan  AFG               -0.988032                      -2.649407   
3          angola  AGO               -0.777283                      -0.311101   
4        anguilla  AIA                     NaN                       1.367357   
..            ...  ...                     ...                            ...   
207        jersey  JEY                1.294189                       1.296690   
210  south africa  ZAF                0.670388                      -0.217931   
211         congo  ZAR               -1.365966                      -1.808007   
212        zambia  ZMB               -0.286199                      -0.102216   
213      zimbabwe  ZWE               -1.141875                      -0.920179   

     GovernmentEffectiveness  RegulatoryQuality  RuleofLaw  \
0                   1.029933           0.857360   1.263128   
1                   1.908749           1.228176   1.579939   
2                  -1.463875          -1.120555  -1.713527   
3                  -1.117144          -0.893871  -1.054343   
4                   0.815824           0.846231   0.355737   
..                       ...                ...        ...   
207                 1.237505           0.922742   1.745989   
210                 0.367380           0.156172  -0.076408   
211                -1.627429          -1.509667  -1.786088   
212                -0.675215          -0.554269  -0.462069   
213                -1.205337          -1.463199  -1.257009   

     ControlofCorruption  
0               1.217238  
1               1.234392  
2              -1.401076  
3              -1.054683  
4               1.234392  
..                   ...  
207             1.043699  
210             0.084924  
211            -1.538931  
212            -0.640345  
213            -1.238796  

[137 rows x 8 columns]

Check pandas profile for any glaring issues (i.e. need to have unique countries)

In [332]:
ProfileReport(df=common)

we've now joined our two datasets, which are ready for joining with the covid data, after which it will be used for clustering. We output for the next notebook.

In [335]:
hofstede_data.to_csv(HOFSTEDE_CLEANSED)
full_wgi_2019.to_csv(WGI_CLEANSED)
common.to_csv(WGI_HOFSTEDE_CLEANSED)